In [1]:
import numpy as np
import math
# import random
import matplotlib.pyplot as plt
from sklearn import datasets, preprocessing

# from deep_nn_utilities import *

In [2]:
def initialize_parameters(layer_dims):
# layers_dims: array containing dimensions of each layer ex initialize_parameters([5, 4, 3])

    np.random.seed(12)
    parameters = {}
    L = len(layer_dims) # number of layers in nn
    
    for l in range(1, L):
        parameters['W' + str(l)] = np.random.randn(layer_dims[l-1], layer_dims[l]) * 0.01
        parameters['b' + str(l)] = np.zeros((layer_dims[l], 1))
        
        assert(parameters['W' + str(l)].shape == (layer_dims[l-1], layer_dims[l]))
        assert(parameters['b' + str(l)].shape == (layer_dims[l], 1))
#     print([(k, parameters[k].shape) for k, v in parameters.items()])
    return parameters

def linear_forward(A, W, b):
#     print('\nlinear forward')
#     print('W', W.shape, 'A', A.shape)
    Z = np.dot(W.T, A) + b
    
#     print('Z', Z.shape)
    
    assert(Z.shape == (W.shape[1], A.shape[1]))
    cache = (A, W, b)
    
    return Z, cache

def sigmoid(Z):
    A = 1 / (1 + np.exp(-Z))
    cache = Z
    return A, cache

def relu(Z):
    A = np.maximum(0, Z)
    
    assert(A.shape == Z.shape)
    cache = Z
    return A, cache

def softmax(Z):
    t = np.exp(Z)
    A = t / np.sum(t, axis=0)
    cache = Z
    
    return A, cache
    

def neuron_activation(A_prev, W, b, activation):
    if activation == 'sigmoid':
        Z, linear_cache = linear_forward(A_prev, W, b)
        # linear cache: A, W, b
        A, activation_cache = sigmoid(Z)
        # activation cache: Z
        
    elif activation == 'relu':
        Z, linear_cache = linear_forward(A_prev, W, b)
        A, activation_cache = relu(Z)
        
    elif activation == 'softmax':
        Z, linear_cache = linear_forward(A_prev, W, b)
        A, activation_cache = softmax(Z)
        
    assert (A.shape == (W.shape[1], A_prev.shape[1]))
    cache = (linear_cache, activation_cache)
    
    return A, cache

def L_model_forward(X, parameters):
    caches = []
    A = X
    L = len(parameters) // 2 # // is floor division
    
    for l in range(1, L):
        
        A_prev = A
        
        A, cache = neuron_activation(A_prev, parameters['W' + str(l)], parameters['b' + str(l)], 'relu')
        caches.append(cache)

    AL, cache = neuron_activation(A, parameters['W' + str(L)], parameters['b' + str(L)], 'softmax')
    caches.append(cache)
#     print('\n', AL)
#     assert(AL.shape == (1, X.shape[1]))
#     assert(AL.shape == (3, X.shape[1])) # should be  (classes x m)

    return AL, caches

def compute_cost(AL, Y):
    m = Y.shape[1]
#     cost = (-1/m) * np.sum(Y*np.log(AL) + (1-Y)*np.log(1-AL))
    
#     cost = np.squeeze(cost)
#     assert(cost.shape == ())
    print('Y', Y.shape)
    print('AL', AL.shape)
    test = Y*np.log(AL)
    print(test.shape, test[:, 70])
    cost = (-1/m) * np.sum(Y * np.log(AL))
    
    return cost
    
def linear_backward(dZ, cache):
    A_prev, W, b = cache
    m = A_prev.shape[1]
#     print('dZ.shape', dZ.shape, 'A_prev.shape', A_prev.shape, 'W.shape', W.shape)
#     dW = (1/m) * np.dot(dZ, A_prev.T)
    dW = (1/m) * np.dot(A_prev, dZ.T)
    db = (1/m) * np.sum(dZ, axis=1, keepdims=True)
#     dA_prev = np.dot(W.T, dZ)
    dA_prev = np.dot(W, dZ)
    
#     assert (dA_prev.shape == A_prev.shape)
#     assert (dW.shape == W.shape)
#     assert (db.shape == b.shape)
    
    return dA_prev, dW, db

def relu_backward(dA, cache):
    Z = cache
    dZ = np.array(dA, copy=True)
    
    dZ[Z <= 0] = 0
    
    assert (dZ.shape == Z.shape)
    
    return dZ

def sigmoid_backward(dA, cache):
    Z = cache
    s = 1 / (1 + np.exp(-Z))
    dZ = dA * s * (1-s) # dLoss/dA * a(1-a) -- same as dLoss/dA * g_prime(Z)
    
    assert (dZ.shape == Z.shape)
    
    return dZ

def linear_activation_backward(dA, cache, activation):
    linear_cache, activation_cache = cache
    # check here for reverse grad shape bug
    if activation == "relu":
        dZ = relu_backward(dA, activation_cache)
        dA_prev, dW, db = linear_backward(dZ, linear_cache)
        
    elif activation == "sigmoid":
        dZ = sigmoid_backward(dA, activation_cache)
        dA_prev, dW, db = linear_backward(dZ, linear_cache)
       
    elif activation == 'softmax':
        dZ = dA
        dA_prev, dW, db = linear_backward(dZ, linear_cache)
        
    return dA_prev, dW, db

def L_model_backward(AL, Y, caches):
    grads = {}
    L = len(caches)
    m = AL.shape[1]
#     Y = Y.reshape(AL.shape)
    
#     dAL = - (np.divide(Y, AL) - np.divide(1 - Y, 1 - AL)) #derivative of cost function
    dAL = AL - Y
#     print('dAL.shape', dAL.shape)
    current_cache = caches[L-1]
    grads["dA" + str(L)], grads["dW" + str(L)], grads["db" + str(L)] = linear_activation_backward(dAL, current_cache, "softmax")
    
    for l in reversed(range(L-1)):
        current_cache = caches[l]
        dA_prev_temp, dW_temp, db_temp = linear_activation_backward(grads["dA" + str(l+2)], current_cache, "relu")
        grads["dA" + str(l+1)] = dA_prev_temp
        grads["dW" + str(l+1)] = dW_temp
        grads["db" + str(l+1)] = db_temp
            
    return grads

def update_parameters(parameters, grads, learning_rate):
    L = len(parameters) // 2      
#     print('\nupdate parameters')                               
#     print([(k, parameters[k].shape) for k, v in parameters.items()])
#     print('grads')
#     print([(k, grads[k].shape) for k, v in grads.items()])
    for l in range(1, L+1):
        parameters['W'+str(l)] = parameters['W'+str(l)] - learning_rate * grads['dW'+str(l)]
        parameters['b'+str(l)] = parameters['b'+str(l)] - learning_rate * grads['db'+str(l)]
        
    return parameters

def predict(X, y, parameters):
    print('X', X.shape, 'Y.shape', y.shape)
    m = X.shape[1]
    n = len(parameters) // 2
    p = np.zeros((y.shape[0], m))
    acc = []
    probas, caches = L_model_forward(X, parameters)
    print('probas\n', probas.shape)
    # max for each example
    # search for index == max
    # assign 1 to that class and 0 to the others
    for i in range(0, probas.shape[1]):
#         print(probas[:, i])
        index = np.where(probas[:, i] == np.max(probas[:, i]))
        probas[index, i] = 1
        zeros = np.where(probas[:, i] != 1)
        probas[zeros, i] = 0
        if np.where(probas[:,i] == 1) == np.where(y[:,i] ==1):
            acc.append(True)
#         print(probas[:, i], 'probas')
#         print(y[:, i], 'y')
#         print(np.where(probas[:,i] == 1) == np.where(y[:,i] ==1))
#         probas[:, i][probas != 1] = 0
#         print(index)
#         print(np.max(probas[:,i]))
#         if probas[0, i] > 0.5:
#             p[0, i] = 1
#         else:
#             p[0, i] = 0
    print(type(probas))
    print("Accuracy: " + str(sum(acc)/m))
#     print("Accuracy: "  + str(np.sum((p == y)/m)))
        
    return p

In [3]:
def L_layer_model(X, Y, layer_dims, learning_rate = .0075, num_iterations = 10, print_cost = False):
    np.random.seed(3)
    costs = []
    
    parameters = initialize_parameters(layer_dims)
    for i in range(0, num_iterations):
        AL, caches = L_model_forward(X, parameters)
        
        cost = compute_cost(AL, Y)
        grads = L_model_backward(AL, Y, caches)
        
        parameters = update_parameters(parameters, grads, learning_rate)
        
        # Print the cost every 100 training example
        if print_cost and i % 10000 == 0:
            print ("Cost after iteration %i: %f" %(i, cost))
        if print_cost and i % 10000 == 0:
            costs.append(cost)
            
    # plot the cost
    plt.plot(np.squeeze(costs))
    plt.ylabel('cost')
    plt.xlabel('iterations (per tens)')
    plt.title("Learning rate =" + str(learning_rate))
    plt.show()
    
    return parameters

In [4]:
wine = datasets.load_wine(True)

In [5]:
iris = datasets.load_iris(True)
iris[0].shape[0]
X = iris[0].T
X = preprocessing.scale(X)

Y_cat = iris[1]
Y = []
for i in Y_cat:
    if i==0:
        Y.append([1,0,0])
    elif i == 1:
        Y.append([0,1,0])
    elif i == 2:
        Y.append([0,0,1])
Y = np.array(Y).T
# split into training/test
# Y = Y[:, :5]
# print('X.shape', X.shape)
# print('Y.shape', Y.shape)
# iris
#normalize data
# l2 regularization
# gradient checking
# X.mean(axis=0)
# X.std(axis=0)

In [6]:
np.random.seed(10)
split = np.random.rand(X.shape[1])

In [7]:

train = split < .7
test = split >= .7
X_train = X[:, train]
Y_train = Y[:, train]
X_test = X[:, test]
Y_test = Y[:, test]

# train = split < .6
# cv = (.6 <= split) & (split < .8)
# test = .8 <= split

# X_train = X[:, train]
# X_cv = X[:, cv]
# X_test = X[:, test]

# Y_train = Y[:, train]
# Y_cv = Y[:, cv]
# Y_test = Y[:, test]

print(X_train.shape, Y_train.shape)
# print(X_cv.shape, Y_cv.shape)
print(X_test.shape, Y_test.shape)




(4, 112) (3, 112)
(4, 38) (3, 38)


In [8]:
# create dummy data in three distinct categories of magnitude, X: [3,30]
inputs = X.shape[0]
m = X.shape[1]
# layer_dims = [inputs, 3, 4, 5, 3]
layer_dims = [inputs, 3, 8, 5, 3] # best architecture so far
# layer_dims = [inputs, 3, 4, 8, 3]

In [ ]:
parameters = L_layer_model(X_train, Y_train, layer_dims, .1, 200000, True)

Y (3, 112)
AL (3, 112)
(3, 112) [-1.09861229 -0.         -0.        ]
Cost after iteration 0: 1.098612
Y (3, 112)
AL (3, 112)
(3, 112) [-1.10069581 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1027132 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.10466548 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.10655475 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.10838302 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.11015227 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.11186439 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.11352122 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.11512454 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.11667608 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1181775 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.11963043 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.12103642 -0.         -0.   

Y (3, 112)
AL (3, 112)
(3, 112) [-1.16211891 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16215221 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16218444 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16221563 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16224581 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16227502 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16230328 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16233064 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16235711 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16238272 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16240751 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1624315 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16245471 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16247718 -0.         -0.        ]
Y (3, 112)
AL (3, 112)


Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314903 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314908 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314914 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314919 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314925 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631493 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314934 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314939 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314944 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314948 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314952 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314957 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314961 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16314964 -0.         -0.        ]
Y (3, 112)
AL (3, 112)


(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631508 -0.        -0.       ]
Y (3, 112)
AL (3, 

Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315081 -0.         -0.        ]
Y (3, 112)
AL (3, 11

...

Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315072 -0.         -0.        ]
Y (3, 112)
AL (3, 11

(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.1631507

Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 11

Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 11

Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 112)
(3, 112) [-1.16315071 -0.         -0.        ]
Y (3, 112)
AL (3, 11

In [ ]:
# p = predict(X_cv, Y_cv, parameters)
# print('p.shape', p.shape)

In [ ]:
p = predict(X_test, Y_test, parameters)
print('p.shape', p.shape)

In [ ]:
p_train = predict(X_train, Y_train, parameters)
print('p.shape', p.shape)